# Model-checking ecological state-transition graphs (S5 Notebook)

## Borana vegetation pathways model

Computation of the STG.

In [1]:
# print the execution time
%time
# compute the Borana model 
%run -m ecco plos-2022.rr

controls = ["Alt", "Fb", "Cb", "Wl", "Ps", "Ig", "BLv"]
# build the STG
G = model()
# split the initial states (one per scenarios)
v = G.split(topo.INIT)
# print the model statistics
print(f"The STG has {sum ([len(c) for c in G])} states encompassing {sum ([len(v[i]) for i in v.isin('INIT')])} scenarios.")

v = G.split(*controls)
print(f"The largest scenario subgraph has {max([len(c) for c in v])} states.")

CPU times: user 4 µs, sys: 1 µs, total: 5 µs
Wall time: 9.3 µs
The STG has 1185 states encompassing 128 scenarios.
The largest scenario subgraph has 26 states.


The system description of the Borana model (variables and ruleset, corresponding to Tab.1 and S2 Table):

In [2]:
model.rr

HTML(value="<pre style='font-family:mono;line-height:140%;'><span style='font-weight:bold;color:#008;'>variabl…

## Comparison with Liao's STMs

Based on the vegetation classes of [(Liao et al. 2018a, Tab. 1)](https://doi.org/10.1002/ece3.4621) we defined vegetation classes as state properties (presence and absence of vegetation variables), see S4 Table. The variables noted with "+" are present, those with "-" are absent, while those with "\*" can be either present or absent.

| Vegetation Class  &nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;  &nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;    | State Description  &nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;  &nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;&nbsp; &nbsp;      |
|:-|:-|
| Closed Canopy Woodland  | $\texttt{Gr-, Sh-, Tr+, Sa*, Cr-}$  |
| Dense Scrubland         | $\texttt{Gr-, Sh+, Tr+, Sa*, Cr-}$  |
| Bushland                | $\texttt{Gr-, Sh+, Tr-, Sa*, Cr-}$  |
| Open Canopy Woodland    | $\texttt{Gr+, Sh-, Tr+, Sa*, Cr-}$  |
| Sparse Scrubland        | $\texttt{Gr+, Sh+, Tr*, Sa*, Cr-}$  |
| Cultivated Land         | $\texttt{Gr-, Sh-, Tr*, Sa-, Cr+}$  |
| Grassland               | $\texttt{Gr+, Sh-, Tr-, Sa-, Cr-}$  |
| Sparsely Vegetated Land | $\texttt{Gr-, Sh-, Tr-, Sa-, Cr-}$  |

In [3]:
VegetationClass = {}
VegetationClass["ClosedCanopyWoodland"] = "(~Gr & ~Sh & Tr & ~Cr)"
VegetationClass["DenseScrubland"] = "(~Gr & Sh & Tr & ~Cr)"
VegetationClass["Bushland"] = "(~Gr & Sh & ~Tr & ~Cr)"
VegetationClass["OpenCanopyWoodland"] = "(Gr & ~Sh & Tr & ~Cr)"
VegetationClass["SparseScrubland"] = "(Gr & Sh & ~Cr)"
VegetationClass["Cropland"] = "(~Gr & ~Sh & ~Sa & Cr)"
VegetationClass["Grassland"] = "(Gr & ~Sh & ~Tr & ~Sa & ~Cr)"
VegetationClass["SparselyVegetatedLand"] = "(~(Gr | Sh | Tr | Sa | Cr))"

In order to compare various scenarios our Borana model with Liao's STMs [(Liao et al. 2018b, Fig. 5)](https://doi.org/10.1016/j.agee.2017.10.009), we split the states of the Borana model between the vegetation classes. Thus the STGs drawn below aggregate the states of our Borana model into vegetation classes. An edge is drawn between two vegetation classes if and only if there is at least one transition in the STG of the model from a state of the first vegetation class to a state of the second vegetation class. Those edges are labelled with the corresponding rules of the model's STG.

Nodes (vegetation classes) decorated with a downward triangle contain initial states, nodes decorated with a circle contain cyclic pathways. The nodes colors are chosen arbitrarily.

### Computation of Fig.6

The blue rounded boxes of Fig.6 gathering the states within the same vegetation classes are displayed here as node colors, i.e. the nodes with the same color are within the same box.

In [4]:
# compute the STG with Pastoralism, Cropban and without Fireban, Intensive Grazing, Wildlife and Browsing Livestock
g = model(_init="Alt+,Fb-,Cb+,Wl+,Ps-,Ig-,BLv-")
# split into vegetation classes
v = g.split(**VegetationClass)
v = v.explicit()
vcls = set(VegetationClass)
def mklbl(row):
    consts = [c[:-1] for c in row.consts if c[:-1] not in controls and c[-1] == "+"]
    return f"{row.ISIN & vcls} / {', '.join(sorted(consts))}"
v.n["lbl"] = mklbl
# draw the graph
v.draw(nodes_label="lbl", nodes_fill_color="component", edges_label="")

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

### Before livestock introduction

In [5]:
# compute the STG without Fireban, Pastoralism (and related policies), but with Cropban and Wildlife
g = model(_init="Alt*,Fb-,Cb+,Wl+,Ps-,Ig-,BLv-")
# split into vegetation classes
v = g.split(**VegetationClass)
v.n["lbl"] = lambda row: row.EQUALS & vcls
# draw the graph
v.draw(nodes_label="lbl", edges_label="tags")

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

The STG and the STM of [(Liao et al. 2018b, Fig. 5A)](https://doi.org/10.1016/j.agee.2017.10.009), figure redone with author's permission, are almost identical:

![](plos-2022-1.svg)

The only difference is the the additional labels "browsing" and "low fire" on the transition between sparse scrubland and grassland. Indeed those events may happen in sparse scrubland before the establishment of trees.

### With livestock and fire

In [6]:
# compute the STG with Pastoralism, Cropban and without Fireban, Intensive Grazing, Wildlife and Browsing Livestock
g = model(_init="Alt*,Fb-,Cb+,Wl-,Ps+,Ig-,BLv-")
# split into vegetation classes
v = g.split(**VegetationClass)
v.n["lbl"] = lambda row: row.EQUALS & vcls
# draw the graph
v.draw(nodes_label="lbl", edges_label="tags")

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

The STG and the STM of [(Liao et al. 2018b, Fig. 5B)](https://doi.org/10.1016/j.agee.2017.10.009), figure redone with author's permission, are almost identical::

![](plos-2022-2.svg)

The only difference is the the additional label "low fire" on the transition between sparse scrubland and grassland. Indeed this event may happen in sparse scrubland before the establishment of trees.

### With intensive grazing and fireban

In [7]:
# compute the STG with Fireban, Intensive Grazing, Cropban, and without Wildlife and Browsing Livestock, starting both from Grassland and Open Canopy Woodland
g = model(_init="Alt*,Fb+,Cb+,Wl-,Ps+,Ig+,BLv-,Tr*")
# split into vegetation classes
v = g.split(**VegetationClass)
v.n["lbl"] = lambda row: row.EQUALS & vcls
# draw the graph
v.draw(nodes_label="lbl", edges_label="tags")

HTML(value='<p style="line-height:140%"><span style="color:#BF7C00; font-weight:bold;">[warning]</span> proper…

The STG is similar to the STM of [(Liao et al. 2018b, Fig. 5C)](https://doi.org/10.1016/j.agee.2017.10.009), figure redone with author's permission: 

![](plos-2022-3.svg)

Some of the extra transitions were empirically observed, such as the transition between Dense Scrubland and Closed Canopy Woodland, as well as the extra vegetation classes [(Liao et al. 2018a, Tab. 1, Fig. 5)](https://doi.org/10.1002/ece3.4621), in particular sparse scrubland is described as a transitory state between grassland and dense scrubland. The main features of the STM: (1) that encroachment is not reversible, are encounterd again in the STG, and (2) that open canopy woodland is not reachable from grassland. See also [(Liao thesis, 2016, Fig. 6 p31)](https://hdl.handle.net/1813/43578) for a STG representation of [(Liao et al. 2018a, Fig. 5)](https://doi.org/10.1002/ece3.4621).

## Scenario selection by model-checking

| English description of the pattern | CTL Formula &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp;  |
|:-|:-|
| **Reachability  pattern** |  |
| &nbsp; &nbsp; &nbsp; An $x$ state *can* be reached | $EF(x)$ |
| &nbsp; &nbsp; &nbsp; An $x$ state *cannot* be reached | $\neg EF(x)$ |
| **Consequence pattern** |  |
| &nbsp; &nbsp; &nbsp; If an $x$ state is reached, then it is *possibly* followed by an $y$ state | $AG(x \Rightarrow EF(y))$ |
| &nbsp; &nbsp; &nbsp; If an $x$ state is reached, then it is *necessarily* followed by an $y$ state | $AG(x \Rightarrow AF(y))$ |
| **Sequence pattern** |  |
| &nbsp; &nbsp; &nbsp; An $y$ state is reachable and is *possibly* preceded *at some time* by an $x$ state | $EF(x \land EF(y))$ |
| &nbsp; &nbsp; &nbsp; An $y$ state is reachable and is *possibly* preceded *all the time* by an $x$ state | $E(x U y)$ |
| &nbsp; &nbsp; &nbsp; An $y$ state is reachable and is *necessarily* preceded *at some time* by an $x$ state &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; | $EF(y) \land \neg E( \neg x U y)$ |
| &nbsp; &nbsp; &nbsp; An $y$ state is reachable and is *necessarily* preceded *all the time* by an $x$ state | $EF(y) \land AG(\neg x \Rightarrow AG(\neg y))$ |
| **Invariance pattern** |  |
| &nbsp; &nbsp; &nbsp; $x$ states *can* persist forever | $EG(x)$ |
| &nbsp; &nbsp; &nbsp; $x$ states *must* persist forever | $AG(x)$ |
| &nbsp; &nbsp; &nbsp; $x$ states *possibly* remain forever reachable | $EG(EF(x))$ |
| &nbsp; &nbsp; &nbsp; $x$ states *necessarily* remain forever reachable | $AG(EF(x))$ |
| &nbsp; &nbsp; &nbsp; $x$ states are *necessarily* reached infinitely often | $AG(AF(x))$ |
| **Reachability & Invariance pattern** | |
| &nbsp; &nbsp; &nbsp; It is *possible* to reach a state from which $x$ states *can* persist forever | $EF(EG(x))$ |
| &nbsp; &nbsp; &nbsp; It is *possible* to reach a state from which $x$ states *must* persist forever | $EF(AG(x))$ |

The queries are built upon the following state properties :

-  Closed canopy woodland is a vegetation class modelled by the presence and absence of plant variables : $$\texttt{ClosedCanopyWoodland} = \texttt{Gr-} \land \texttt{Sh-} \land \texttt{Tr+} \land \texttt{Cr-}$$

- Encroachment is modelled by the vegetation classes with trees or shrubs but without grasses nor crops (closed canopy woodland, dense scrubland and bushland) : $$\texttt{Encroachment} = (\texttt{Tr+} \lor \texttt{Sh+}) \land \texttt{Gr-} \land \texttt{Cr-}$$

- Subsistence production is modelled by the states with livestock or crops : $$\texttt{Subsistence} = \texttt{Lv+} \lor \texttt{Cr+}$$

In [8]:
closed_canopy_woodland = "(~Gr & ~Sh & Tr & ~Cr)"
encroachment = "((Tr | Sh) & ~Gr & ~Cr)"
subsistence = "(Lv | Cr)"

### Reachability pattern : EF(Encroachment)

Pattern : $\exists F (\texttt{Encroachment})$

Pattern description : An encroached state can be reached.

In [9]:
%%time
# translation of the pattern into a CTL formula f
f = f"EF({encroachment})"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls)

CPU times: user 294 ms, sys: 310 µs, total: 294 ms
Wall time: 294 ms


Ig & Ps

Encroachment can only happen under the scenarios encompassing pastoralism $\texttt{Ps+}$ with intensive grazing $\texttt{Ig+}$.

### Reachability pattern : EF(ClosedCanopyWoodland)

Pattern : $\exists F (\texttt{ClosedCanopyWoodland})$

Pattern description : Closed Canopy Woodland can be reached.

In [10]:
%%time
# translation of the pattern into a CTL formula f
f = f"EF({closed_canopy_woodland})"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls)

CPU times: user 277 ms, sys: 29 µs, total: 277 ms
Wall time: 276 ms


Ig & Ps & (Alt | BLv | Wl | ~Fb)

Closed Canopy Woodland can only happen under pastoralism $\texttt{Ps+}$ with intensive grazing $\texttt{Ig+}$ and with at least one of the following factors: high altitude $\texttt{Alt+}$, no fire ban $\texttt{Fb-}$, presence of wildlife $\texttt{Wl+}$, browsing livestock $\texttt{BLv+}$.

### Reachability + Consequence pattern : EF(Encroachment) & AG(Encroachment => EF(!Encroachment))

Pattern : $\exists F(\texttt{Encroachment}) \land \forall G ( \texttt{Encroachment} => \exists F(\neg \texttt{Encroachment}))$

Pattern description : An encroached state is reachable, and whenever it is reached it is possibly followed by an unencroached state, i.e. it is reversible.

In [11]:
%%time
# translation of the pattern into a CTL formula f
f = f"EF({encroachment}) & (AG({encroachment} => EF(~({encroachment}))))"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls, normalise="dnf")

CPU times: user 113 ms, sys: 283 µs, total: 114 ms
Wall time: 113 ms


Alt & Ig & Ps & ~Cb

If an encroached state is reachable ($\texttt{Ps+} \land \texttt{Ig+}$, see query 1) and if the system is at high altitude $\texttt{Alt+}$ with crops allowed $\texttt{Cb-}$, then whenever an encroached state is reached it is possibly followed by an unencroached state.

### Sequence pattern : EF(Encroachment & EF(!Encroachment))

Pattern : $\exists F(\texttt{Encroachment} \land \exists F(\neg\texttt{Encroachment}))$

Pattern description : An unencroached state is reachable and is possibly preceded at some time by an encroached state, i.e. at least some encroachment pathways are reversible.

In [12]:
%%time
# translation of the pattern into a CTL formula f
f = f"EF({encroachment} & EF(~{encroachment}))"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls, normalise="dnf")

CPU times: user 181 ms, sys: 3.08 ms, total: 184 ms
Wall time: 183 ms


(BLv & Ig & Ps) | (Ig & Ps & Wl) | (Alt & Ig & Ps & ~Cb)

If an encroached state is reachable ($\texttt{Ps+} \land \texttt{Ig+}$, see query 1), there are three set of scenarios where at least some encroachment pathways are reversible: (1) with browsing livestock $\texttt{BLv}+$, (2) with wildlife $\texttt{Wl+}$, (3) at high altitude $\texttt{Alt+}$ with crops allowed $\texttt{Cb-}$.

### Invariance pattern : AG(EF(Subsistence))

Pattern : $\forall G(\exists F(\texttt{Subsistence}))$

Pattern description : Subsistence states necessarily remain forever reachable.

In [13]:
%%time
# translation of the pattern into a CTL formula f
f = f"AG(EF({subsistence}))"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls, normalise="dnf")

CPU times: user 251 ms, sys: 0 ns, total: 251 ms
Wall time: 250 ms


(Ps & ~Ig) | (Alt & Ps & ~Cb) | (Alt & Wl & ~Cb)

There are three sets of scenarios where subsistence remains reachable whatever happens : (1) under pastoralism $\texttt{Ps+}$ without intensive grazing $\texttt{Ig-}$, (2) at high altitude $\texttt{Alt+}$ with crops allowed $\texttt{Cb-}$ and with pastoralism $\texttt{Ps+}$ , or (3) at high altitude $\texttt{Alt+}$ with crops allowed $\texttt{Cb-}$ and with wildlife $\texttt{Wl+}$.

### Reachability & Invariance pattern : EF(EG(Subsistence))

Pattern : $\exists F(\exists G(\texttt{Subsistence}))$

Pattern description : It is possible to reach a state from which the subsistence can persist forever.

In [14]:
%%time
# translation of the pattern into a CTL formula f
f = f"EF(EG({subsistence}))"
# split the states whether they satisfy f or not
v = G.split(f)
# split the states whether they are initial or not
v = v.split("INIT")
# print the scenarios satisfying f
v.form(*(v.isin(f) & v.isin("INIT")), variables=controls, normalise="dnf")

CPU times: user 238 ms, sys: 4.14 ms, total: 242 ms
Wall time: 241 ms


(BLv & Ps) | (Ps & ~Alt) | (Cb & Fb & Ps & ~Ig)

There are three sets of scenarios where it is possible to reach a state from which subsistence can persist forever: (1) under pastoralism $\texttt{Ps+}$ with browsing livestock $\texttt{BLv+}$, (2) at low altitude $\texttt{Alt-}$ with pastoralism $\texttt{Ps+}$, or (3) with fire banned $\texttt{Fb+}$ as well as crops $\texttt{Cb+}$ and with pastoralism $\texttt{Ps+}$ but without intensive grazing $\texttt{Ig-}$.